In [3]:
import os
import random
import numpy as np
import sys
import torch
import pprint

root = '/'
pprint.pprint(sys.path)

sys.path.append(import_path)
pprint.pprint(sys.path)

1

In [4]:
import os
import sys
import pprint

import_path = root + 'pigvae_all'
sys.path.append(import_path)
pprint.pprint(sys.path)

import_path1 = root + 'pigvae_all/pigvae'
sys.path.append(import_path1)
pprint.pprint(sys.path)

import_path2 = root + 'ddpm-torch'
sys.path.append(import_path2)
pprint.pprint(sys.path)

['/opt/conda/lib/python310.zip',
 '/opt/conda/lib/python3.10',
 '/opt/conda/lib/python3.10/lib-dynload',
 '',
 '/opt/conda/lib/python3.10/site-packages',
 'pigvae_all']
['/opt/conda/lib/python310.zip',
 '/opt/conda/lib/python3.10',
 '/opt/conda/lib/python3.10/lib-dynload',
 '',
 '/opt/conda/lib/python3.10/site-packages',
 'pigvae_all',
 'ddpm-torch']


In [5]:
import numpy as np
import torch
from torch.utils.data import Dataset
from torch.utils.data.distributed import DistributedSampler
import random
#import pytorch_lightning as pl
from torch_geometric.data import Data
from torch_geometric.utils import from_networkx
import networkx as nx
from networkx.algorithms.shortest_paths.dense import floyd_warshall_numpy

from networkx.generators.random_graphs import *
from networkx.generators.ego import ego_graph
from networkx.generators.geometric import random_geometric_graph

/opt/conda/lib/python3.10/site-packages/torch_geometric/typing.py:86: UserWarning: An issue occurred while importing 'torch-scatter'. Disabling its usage. Stacktrace: /opt/conda/lib/python3.10/site-packages/torch_scatter/_version_cpu.so: undefined symbol: _ZN5torch3jit17parseSchemaOrNameERKSsb
  warnings.warn(f"An issue occurred while importing 'torch-scatter'. "
/opt/conda/lib/python3.10/site-packages/torch_geometric/typing.py:97: UserWarning: An issue occurred while importing 'torch-cluster'. Disabling its usage. Stacktrace: /opt/conda/lib/python3.10/site-packages/torch_cluster/_version_cpu.so: undefined symbol: _ZN5torch3jit17parseSchemaOrNameERKSsb
  warnings.warn(f"An issue occurred while importing 'torch-cluster'. "
/opt/conda/lib/python3.10/site-packages/torch_geometric/typing.py:113: UserWarning: An issue occurred while importing 'torch-spline-conv'. Disabling its usage. Stacktrace: /opt/conda/lib/python3.10/site-packages/torch_spline_conv/_version_cpu.so: undefined symbol: _ZN

In [7]:
loaded_data = torch.load(root + 'dataset/train_dataset/zinc_gdata/tensor_data.pkl')

# 各テンソルにアクセス
node_features = loaded_data['node_features']
edge_features = loaded_data['edge_features']
mask = loaded_data['mask']
props = loaded_data['props']

In [8]:
num_node_f, num_edge_f = 43, 6

In [9]:
node_features.shape, edge_features.shape, mask.shape, props.shape

(torch.Size([75000, 26, 43]),
 torch.Size([75000, 26, 26, 13]),
 torch.Size([75000, 26]),
 torch.Size([75000]))

In [10]:
train_dataset = torch.utils.data.TensorDataset(node_features[0:50000], edge_features[0:50000], mask[0:50000], props[0:50000])
val_dataset = torch.utils.data.TensorDataset(node_features[50000:60000], edge_features[50000:60000], mask[50000:60000], props[50000:60000])
test_dataset = torch.utils.data.TensorDataset(node_features[60000:70000], edge_features[60000:70000], mask[60000:70000], props[60000:70000])

In [11]:
n_batch = 20

train_loader = torch.utils.data.DataLoader(train_dataset, batch_size=n_batch, shuffle=True)
val_loader = torch.utils.data.DataLoader(val_dataset, batch_size=n_batch, shuffle=False)
test_loader = torch.utils.data.DataLoader(test_dataset, batch_size=n_batch, shuffle=False)

In [12]:
device = torch.device('cuda:0' if torch.cuda.is_available() else 'cpu')

In [13]:
hparams = {
    "vae":True,
    "kld_loss_scale":0.01,
    "perm_loss_scale":0.1,
    "property_loss_scale":0.5,
    "num_node_features":num_node_f,
    "num_edge_features":6+num_edge_f+1,
    "emb_dim": 90,
    'graph_encoder_hidden_dim': 256,
    'graph_encoder_k_dim': 64,
    'graph_encoder_v_dim': 64,
    'graph_encoder_num_heads': 16,
    'graph_encoder_ppf_hidden_dim': 512,
    'graph_encoder_num_layers': 16,
    'graph_decoder_hidden_dim': 256,
    'graph_decoder_k_dim': 64,
    'graph_decoder_v_dim': 64,
    'graph_decoder_num_heads': 16,
    'graph_decoder_ppf_hidden_dim': 512,
    'graph_decoder_num_layers': 16,
    "graph_decoder_pos_emb_dim": 64,
    'property_predictor_hidden_dim': 3,
    'num_properties': 1
}

model_save_dir = root + 'save_models/zinc/pig-beta-diffvae_models/'

if not os.path.exists(model_save_dir):
    os.makedirs(model_save_dir)

## Denoising Model Calss

In [14]:
import os
import torch
import numpy as np
from torch.optim import Adam, lr_scheduler
from ddpm_torch.utils import seed_all, infer_range
from ddpm_torch.toy import *

import torch
import torch.nn as nn

from ddpm_torch.modules import Linear, Sequential
from ddpm_torch.functions import get_timestep_embedding


DEFAULT_NORMALIZER = nn.LayerNorm
DEFAULT_NONLINEARITY = nn.LeakyReLU(negative_slope=0.02, inplace=True)


class TemporalLayer(nn.Module):
    normalize = DEFAULT_NORMALIZER
    nonlinearity = DEFAULT_NONLINEARITY

    def __init__(self, in_features, out_features, temporal_features):
        super(TemporalLayer, self).__init__()
        self.norm1 = self.normalize(in_features)
        self.fc1 = Linear(in_features, out_features, bias=False)
        self.norm2 = self.normalize(out_features)
        self.fc2 = Linear(out_features, out_features, bias=False)
        self.enc = Linear(temporal_features, out_features)

        self.skip = nn.Identity() if in_features == out_features else Linear(in_features, out_features, bias=False)

    def forward(self, x, t_emb):
        out = self.fc1(self.nonlinearity(self.norm1(x)))
        out += self.enc(t_emb)
        out = self.fc2(self.nonlinearity(self.norm2(out)))
        skip = self.skip(x)
        return out + skip


class Denoiser(nn.Module):
    normalize = DEFAULT_NORMALIZER
    nonlinearity = DEFAULT_NONLINEARITY

    def __init__(self, in_features, mid_features, num_temporal_layers):
        super(Denoiser, self).__init__()

        self.in_fc = Linear(in_features, mid_features, bias=False)
        self.temp_fc = Sequential(*([TemporalLayer(
            mid_features, mid_features, mid_features), ] * num_temporal_layers))
        self.out_norm = self.normalize(mid_features)
        self.out_fc = Linear(mid_features, in_features)
        self.t_proj = nn.Sequential(
            Linear(mid_features, mid_features),
            self.nonlinearity)
        self.mid_features = mid_features

    def forward(self, x, t):
        t_emb = get_timestep_embedding(t, self.mid_features)
        t_emb = self.t_proj(t_emb)
        out = self.in_fc(x)
        out = self.temp_fc(out, t_emb=t_emb)
        out = self.out_fc(self.out_norm(out))
        return out

In [15]:
# denoising model parameters
model_mean_type = "eps"
model_var_type = "fixed-large"
loss_type = "mse"
lat_dim = 90
in_features = lat_dim
out_features = 2 * in_features if model_var_type == "learned" else in_features
mid_features = 256
num_temporal_layers = 3

In [16]:
# diffusion parameters
beta_schedule = "linear"
beta_start, beta_end = 0.001, 0.2
timesteps = 200
betas = get_beta_schedule(beta_schedule, beta_start=beta_start, beta_end=beta_end, timesteps=timesteps)

## Graph Latent Diffusion Variational Autoencoder Class

In [17]:
from pigvae.models import GraphEncoder, GraphDecoder, Permuter
from pigvae.models import BottleNeckEncoder, BottleNeckDecoder, PropertyPredictor

import torch
from torch.nn import Linear, LayerNorm, Dropout
from torch.nn.functional import relu, pad
from pigvae.graph_transformer import Transformer, PositionalEncoding
from pigvae.synthetic_graphs.data import DenseGraphBatch


class GraphLDA(torch.nn.Module):
    def __init__(self, hparams):
        super().__init__()
        #self.vae = hparams["vae"]
        self.encoder = GraphEncoder(hparams)
        self.bottle_neck_encoder = BottleNeckEncoder(hparams)
        self.bottle_neck_decoder = BottleNeckDecoder(hparams)
        self.property_predictor = PropertyPredictor(hparams)
        self.permuter = Permuter(hparams)
        self.decoder = GraphDecoder(hparams)

        self.dense_fn = Denoiser(in_features, mid_features, num_temporal_layers)
        self.diffusion = GaussianDiffusion(betas=betas, model_mean_type=model_mean_type, model_var_type=model_var_type, loss_type=loss_type)

    def encode(self, node_features, edge_features, mask):

        graph_emb, node_features = self.encoder(
            node_features=node_features,
            edge_features=edge_features,
            mask=mask,
        )
        graph_emb, mu, logvar = self.bottle_neck_encoder(graph_emb)
        return  graph_emb, mu, logvar, node_features

    def decode(self, graph_emb, perm, mask=None):
        props = self.property_predictor(graph_emb).squeeze()

        """
        if mask is None:
            num_nodes = torch.round(props * STD_NUM_NODES + MEAN_NUM_NODES).long()
            mask = torch.arange(max(num_nodes)).type_as(num_nodes).unsqueeze(0) < num_nodes.unsqueeze(1)
        """

        graph_emb = self.bottle_neck_decoder(graph_emb)
        node_logits, edge_logits = self.decoder(
            graph_emb=graph_emb,
            perm=perm,
            mask=mask
        )

        return node_logits, edge_logits, props

    def forward(self, node_features, edge_features, mask, training, tau):
        graph_emb, mu, logvar, node_features = self.encode(node_features, edge_features, mask)
        perm = self.permuter(node_features, mask=mask, hard=not training, tau=tau)

        #diffusion process
        z_0 = graph_emb
        B = z_0.shape[0]
        T = self.diffusion.timesteps
        t = torch.randint(T, size=(B, ), dtype=torch.int64, device=device)
        t_noise = torch.randn_like(graph_emb)
        z_t = self.diffusion.q_sample(z_0, t, noise=t_noise)

        #denoising
        model_out = self.dense_fn(z_t, t) #model_out : 出力, t_noise : 予測するターゲット

        #deocde from noisy latent vector
        graph_pred = self.decode(z_0, perm, mask)

        return graph_pred, perm, graph_emb, mu, logvar, model_out, t_noise

class BottleNeckEncoder(torch.nn.Module):
    def __init__(self, hparams):
        super().__init__()
        self.d_in = hparams["graph_encoder_hidden_dim"]
        self.d_out = hparams["emb_dim"]
        self.w = Linear(self.d_in, 2 * self.d_out)

    def forward(self, x):
        z = self.w(relu(x))

        mu = z[:, :self.d_out]
        logvar = z[:, self.d_out:]
        std = torch.exp(0.5 * logvar)
        eps = torch.randn_like(std)
        z = mu + eps * std

        return z, mu, logvar

In [18]:
model = GraphLDA(hparams).to(device)

In [19]:
from pigvae.synthetic_graphs.critic_zinc import Critic

critic = Critic(hparams, device)
lr=0.00005

optimizer = torch.optim.Adam([
    {'params': model.encoder.parameters()},
    {'params': model.decoder.parameters()},
    {'params': model.bottle_neck_encoder.parameters()},
    {'params': model.bottle_neck_decoder.parameters()},
    {'params': model.property_predictor.parameters()},
    {'params': model.permuter.parameters()},
    {'params': model.dense_fn.parameters(), 'lr': 0.0005}
], lr=lr, betas=(0.9, 0.98))

lr_scheduler = torch.optim.lr_scheduler.ExponentialLR(optimizer=optimizer, gamma=0.9)

# Training

In [20]:
train_loss_list = []
val_loss_list = []

def val_preds(epoch):

    model.eval()

    sum_errors = 0

    for batch_idx, batch_data in enumerate(val_loader):

        with torch.no_grad():

            if torch.cuda.is_available():
                node_features, edge_features, mask, props = batch_data
                node_features, edge_features, mask, props = node_features.to(device), edge_features.to(device), mask.to(device), props.to(device)

            graph_pred, perm, graph_emb, mu, logvar, model_out, t_noise = model(node_features, edge_features, mask, training=True, tau=1.0)
            node_logits, edge_logits, pred_props = graph_pred

            vae_loss = critic(node_features, edge_features, props, node_logits, edge_logits, pred_props, mask, perm, mu, logvar)

            batch_vae_loss = vae_loss['node_loss'] * 10 + vae_loss['edge_loss'] * 10 + vae_loss['perm_loss'] * 0.1
            diffusion_loss = torch.sum((t_noise - model_out).pow(2), dim = 1).mean()
            negative_entropy = - torch.mean(torch.sum(logvar,dim=1))
            batch_all_loss = batch_vae_loss + diffusion_loss * beta + negative_entropy.data * gamma

            if batch_idx % 10 == 0:
                print(vae_loss)
                print("Epoch (val) : ", epoch, "  batch (val) : ", batch_idx , "Loss sum : ", batch_all_loss.data.item(), "dsm : ", diffusion_loss.data.item(), "neg entropy : ", negative_entropy.data.item())

            sum_errors = sum_errors + vae_loss['node_loss'].data.item() * 10 + vae_loss['edge_loss'].data.item() * 10 \
             + diffusion_loss.data.item() * beta + negative_entropy.data.item() * gamma

            del batch_all_loss
            torch.cuda.empty_cache()

    return sum_errors

In [21]:
import datetime

# テキストファイルのパスを指定
log_path = model_save_dir + 'log.txt'

f = open(log_path, 'w')
f.write('train -- logs')
f.close()

def logging_txt(epoch):
    dt_now = datetime.datetime.now()

    # ファイルを読み込んで、末尾の行を取得
    with open(log_path, 'r') as file:
        lines = file.readlines()
        last_line = lines[-1].strip()

    # 末尾の行に追記する文字列を指定
    append_string = "epoch " + str(epoch) + " : " + str(dt_now)

    # ファイルに追記
    with open(log_path, 'a') as file:
        file.write('\n' + append_string)

In [22]:
num_epochs = 100
beta = 0.01
gamma = 1e-4
best_loss = 10000000

for epoch in range(num_epochs):
    model.train()

    sum_errors = 0

    for batch_idx, batch_data in enumerate(train_loader):

        node_features, edge_features, mask, props = batch_data
        node_features, edge_features, mask, props = node_features.to(device), edge_features.to(device), mask.to(device), props.to(device)

        optimizer.zero_grad()

        graph_pred, perm, graph_emb, mu, logvar, model_out, t_noise = model(node_features, edge_features, mask, training=True, tau=1.0)
        node_logits, edge_logits, pred_props = graph_pred

        vae_loss = critic(node_features, edge_features, props, node_logits, edge_logits, pred_props, mask, perm, mu, logvar)

        batch_vae_loss = vae_loss['node_loss'] * 10 + vae_loss['edge_loss'] * 10 + vae_loss['perm_loss'] * 0.1
        diffusion_loss = torch.sum((t_noise - model_out).pow(2), dim = 1).mean()
        negative_entropy = - torch.mean(torch.sum(logvar,dim=1))
        batch_all_loss = batch_vae_loss + diffusion_loss * beta + negative_entropy * gamma

        if batch_idx % 100 == 0:
            print("Epoch : ", epoch, " Batch : ", batch_idx, " Loss : ", batch_all_loss.data.item(), "dsm : ", diffusion_loss.data.item(), "neg entropy : ", negative_entropy.data.item())
            print(vae_loss)

        sum_errors = sum_errors + vae_loss['node_loss'].data.item() * 10 + vae_loss['edge_loss'].data.item() * 10 \
         + diffusion_loss.data.item() * beta + negative_entropy.data.item() * gamma

        batch_all_loss.backward()

        optimizer.step()

        del batch_all_loss
        torch.cuda.empty_cache()

    lr_scheduler.step()

    train_loss_list.append(sum_errors / len(train_loader))
    val_loss = val_preds(epoch) / len(val_loader)
    val_loss_list.append(val_loss)

    np.save(model_save_dir + "train_loss_hist", np.array(train_loss_list))
    np.save(model_save_dir + "val_loss_hist", np.array(val_loss_list))

    logging_txt(epoch)

    if val_loss < best_loss:
        save_model_path = model_save_dir + "pigvae_best_model" + ".pt"
        torch.save(model, save_model_path)

        optimizer_path = model_save_dir + "opt_best_model" + ".pt"
        torch.save(optimizer.state_dict(), optimizer_path)

        best_loss = val_loss

Epoch :  0  Batch :  0  Loss :  14.994648933410645 dsm :  118.6267318725586 neg entropy :  -3.4778435230255127
{'edge_loss': tensor(0.5641, device='cuda:0', grad_fn=<DivBackward0>), 'node_loss': tensor(0.7627, device='cuda:0',
       grad_fn=<BinaryCrossEntropyWithLogitsBackward0>), 'kld_loss': tensor(13.0336, device='cuda:0', grad_fn=<MeanBackward0>), 'perm_loss': tensor(5.4108, device='cuda:0', grad_fn=<AddBackward0>), 'property_loss': tensor(470.1528, device='cuda:0', grad_fn=<MseLossBackward0>)}
Epoch :  0  Batch :  10  Loss :  8.664228439331055 dsm :  104.6242446899414 neg entropy :  2.6926729679107666
{'edge_loss': tensor(0.3446, device='cuda:0', grad_fn=<DivBackward0>), 'node_loss': tensor(0.3608, device='cuda:0',
       grad_fn=<BinaryCrossEntropyWithLogitsBackward0>), 'kld_loss': tensor(18.2393, device='cuda:0', grad_fn=<MeanBackward0>), 'perm_loss': tensor(5.6356, device='cuda:0', grad_fn=<AddBackward0>), 'property_loss': tensor(499.2143, device='cuda:0', grad_fn=<MseLossBack

Epoch :  0  Batch :  170  Loss :  5.635782241821289 dsm :  74.74198150634766 neg entropy :  48.551300048828125
{'edge_loss': tensor(0.2628, device='cuda:0', grad_fn=<DivBackward0>), 'node_loss': tensor(0.1935, device='cuda:0',
       grad_fn=<BinaryCrossEntropyWithLogitsBackward0>), 'kld_loss': tensor(17.7392, device='cuda:0', grad_fn=<MeanBackward0>), 'perm_loss': tensor(3.2123, device='cuda:0', grad_fn=<AddBackward0>), 'property_loss': tensor(526.7475, device='cuda:0', grad_fn=<MseLossBackward0>)}
Epoch :  0  Batch :  180  Loss :  5.47861385345459 dsm :  81.3126449584961 neg entropy :  50.98126983642578
{'edge_loss': tensor(0.2554, device='cuda:0', grad_fn=<DivBackward0>), 'node_loss': tensor(0.1782, device='cuda:0',
       grad_fn=<BinaryCrossEntropyWithLogitsBackward0>), 'kld_loss': tensor(20.1119, device='cuda:0', grad_fn=<MeanBackward0>), 'perm_loss': tensor(3.2461, device='cuda:0', grad_fn=<AddBackward0>), 'property_loss': tensor(502.0894, device='cuda:0', grad_fn=<MseLossBackwa

Epoch :  0  Batch :  340  Loss :  4.035975456237793 dsm :  54.1343994140625 neg entropy :  90.1736068725586
{'edge_loss': tensor(0.2126, device='cuda:0', grad_fn=<DivBackward0>), 'node_loss': tensor(0.1051, device='cuda:0',
       grad_fn=<BinaryCrossEntropyWithLogitsBackward0>), 'kld_loss': tensor(31.8811, device='cuda:0', grad_fn=<MeanBackward0>), 'perm_loss': tensor(3.0828, device='cuda:0', grad_fn=<AddBackward0>), 'property_loss': tensor(480.0602, device='cuda:0', grad_fn=<MseLossBackward0>)}
Epoch :  0  Batch :  350  Loss :  4.090377330780029 dsm :  59.0589714050293 neg entropy :  92.13729858398438
{'edge_loss': tensor(0.2126, device='cuda:0', grad_fn=<DivBackward0>), 'node_loss': tensor(0.1066, device='cuda:0',
       grad_fn=<BinaryCrossEntropyWithLogitsBackward0>), 'kld_loss': tensor(32.4540, device='cuda:0', grad_fn=<MeanBackward0>), 'perm_loss': tensor(2.9889, device='cuda:0', grad_fn=<AddBackward0>), 'property_loss': tensor(469.8315, device='cuda:0', grad_fn=<MseLossBackward

Epoch :  0  Batch :  510  Loss :  3.534212827682495 dsm :  43.67869186401367 neg entropy :  123.79842376708984
{'edge_loss': tensor(0.2072, device='cuda:0', grad_fn=<DivBackward0>), 'node_loss': tensor(0.0697, device='cuda:0',
       grad_fn=<BinaryCrossEntropyWithLogitsBackward0>), 'kld_loss': tensor(45.3213, device='cuda:0', grad_fn=<MeanBackward0>), 'perm_loss': tensor(3.1665, device='cuda:0', grad_fn=<AddBackward0>), 'property_loss': tensor(519.4741, device='cuda:0', grad_fn=<MseLossBackward0>)}
Epoch :  0  Batch :  520  Loss :  3.3237080574035645 dsm :  37.075286865234375 neg entropy :  130.73974609375
{'edge_loss': tensor(0.1953, device='cuda:0', grad_fn=<DivBackward0>), 'node_loss': tensor(0.0686, device='cuda:0',
       grad_fn=<BinaryCrossEntropyWithLogitsBackward0>), 'kld_loss': tensor(45.3873, device='cuda:0', grad_fn=<MeanBackward0>), 'perm_loss': tensor(3.0112, device='cuda:0', grad_fn=<AddBackward0>), 'property_loss': tensor(484.7318, device='cuda:0', grad_fn=<MseLossBack

Epoch :  0  Batch :  680  Loss :  2.9296722412109375 dsm :  27.0084171295166 neg entropy :  158.46714782714844
{'edge_loss': tensor(0.1868, device='cuda:0', grad_fn=<DivBackward0>), 'node_loss': tensor(0.0467, device='cuda:0',
       grad_fn=<BinaryCrossEntropyWithLogitsBackward0>), 'kld_loss': tensor(58.3488, device='cuda:0', grad_fn=<MeanBackward0>), 'perm_loss': tensor(3.0877, device='cuda:0', grad_fn=<AddBackward0>), 'property_loss': tensor(512.1518, device='cuda:0', grad_fn=<MseLossBackward0>)}
Epoch :  0  Batch :  690  Loss :  3.0749659538269043 dsm :  30.231781005859375 neg entropy :  162.06809997558594
{'edge_loss': tensor(0.1980, device='cuda:0', grad_fn=<DivBackward0>), 'node_loss': tensor(0.0505, device='cuda:0',
       grad_fn=<BinaryCrossEntropyWithLogitsBackward0>), 'kld_loss': tensor(58.5969, device='cuda:0', grad_fn=<MeanBackward0>), 'perm_loss': tensor(2.7196, device='cuda:0', grad_fn=<AddBackward0>), 'property_loss': tensor(449.0334, device='cuda:0', grad_fn=<MseLossB

...

Epoch :  48  Batch :  710  Loss :  0.89035564661026 dsm :  0.48342639207839966 neg entropy :  588.4501953125
{'edge_loss': tensor(0.0658, device='cuda:0', grad_fn=<DivBackward0>), 'node_loss': tensor(-0.0025, device='cuda:0',
       grad_fn=<BinaryCrossEntropyWithLogitsBackward0>), 'kld_loss': tensor(254.8960, device='cuda:0', grad_fn=<MeanBackward0>), 'perm_loss': tensor(1.9334, device='cuda:0', grad_fn=<AddBackward0>), 'property_loss': tensor(400.5950, device='cuda:0', grad_fn=<MseLossBackward0>)}
Epoch :  48  Batch :  720  Loss :  0.8912853598594666 dsm :  1.3297961950302124 neg entropy :  593.9816284179688
{'edge_loss': tensor(0.0568, device='cuda:0', grad_fn=<DivBackward0>), 'node_loss': tensor(0.0025, device='cuda:0',
       grad_fn=<BinaryCrossEntropyWithLogitsBackward0>), 'kld_loss': tensor(256.7628, device='cuda:0', grad_fn=<MeanBackward0>), 'perm_loss': tensor(2.2509, device='cuda:0', grad_fn=<AddBackward0>), 'property_loss': tensor(483.0080, device='cuda:0', grad_fn=<MseLoss

Epoch :  48  Batch :  880  Loss :  0.8458415865898132 dsm :  1.6462030410766602 neg entropy :  595.6895751953125
{'edge_loss': tensor(0.0510, device='cuda:0', grad_fn=<DivBackward0>), 'node_loss': tensor(0.0033, device='cuda:0',
       grad_fn=<BinaryCrossEntropyWithLogitsBackward0>), 'kld_loss': tensor(257.6752, device='cuda:0', grad_fn=<MeanBackward0>), 'perm_loss': tensor(2.2762, device='cuda:0', grad_fn=<AddBackward0>), 'property_loss': tensor(514.0535, device='cuda:0', grad_fn=<MseLossBackward0>)}
Epoch :  48  Batch :  890  Loss :  0.9017146825790405 dsm :  1.6194419860839844 neg entropy :  590.0021362304688
{'edge_loss': tensor(0.0570, device='cuda:0', grad_fn=<DivBackward0>), 'node_loss': tensor(0.0031, device='cuda:0',
       grad_fn=<BinaryCrossEntropyWithLogitsBackward0>), 'kld_loss': tensor(255.2909, device='cuda:0', grad_fn=<MeanBackward0>), 'perm_loss': tensor(2.2541, device='cuda:0', grad_fn=<AddBackward0>), 'property_loss': tensor(485.2300, device='cuda:0', grad_fn=<MseL

Epoch :  48  Batch :  1050  Loss :  0.8912141919136047 dsm :  4.659924030303955 neg entropy :  591.0225830078125
{'edge_loss': tensor(0.0581, device='cuda:0', grad_fn=<DivBackward0>), 'node_loss': tensor(-0.0032, device='cuda:0',
       grad_fn=<BinaryCrossEntropyWithLogitsBackward0>), 'kld_loss': tensor(255.4837, device='cuda:0', grad_fn=<MeanBackward0>), 'perm_loss': tensor(2.3622, device='cuda:0', grad_fn=<AddBackward0>), 'property_loss': tensor(503.2958, device='cuda:0', grad_fn=<MseLossBackward0>)}
Epoch :  48  Batch :  1060  Loss :  0.9550340175628662 dsm :  4.40924596786499 neg entropy :  585.4284057617188
{'edge_loss': tensor(0.0579, device='cuda:0', grad_fn=<DivBackward0>), 'node_loss': tensor(0.0035, device='cuda:0',
       grad_fn=<BinaryCrossEntropyWithLogitsBackward0>), 'kld_loss': tensor(253.6368, device='cuda:0', grad_fn=<MeanBackward0>), 'perm_loss': tensor(2.3832, device='cuda:0', grad_fn=<AddBackward0>), 'property_loss': tensor(505.9776, device='cuda:0', grad_fn=<MseL

Epoch :  48  Batch :  1220  Loss :  0.9255467057228088 dsm :  3.620213270187378 neg entropy :  588.8580932617188
{'edge_loss': tensor(0.0579, device='cuda:0', grad_fn=<DivBackward0>), 'node_loss': tensor(0.0031, device='cuda:0',
       grad_fn=<BinaryCrossEntropyWithLogitsBackward0>), 'kld_loss': tensor(254.7446, device='cuda:0', grad_fn=<MeanBackward0>), 'perm_loss': tensor(2.2061, device='cuda:0', grad_fn=<AddBackward0>), 'property_loss': tensor(472.9517, device='cuda:0', grad_fn=<MseLossBackward0>)}


IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)

